In [1]:
import random
import numpy as np
from PIL import Image
import pandas as pd
from tqdm.notebook import tqdm
Image.MAX_IMAGE_PIXELS = None

# LOADING

In [2]:
### Load areas
with open("input files/areas.txt","r") as file:
    contents = file.read().splitlines()

areas = {}
temp = len(contents)
for line in range(0, len(contents)-3, 4):
    name = contents[line].split(' =')[0]
    areas[name] = list(map(int,contents[line+1].split('= { ')[1].split(' }')[0].split(' ')))

### Load regions
with open("input files/regions.txt","r") as file:
    contents = file.read().splitlines()

regions = {}
temp = len(contents)
for line in range(0, len(contents)-3, 4):
    name = contents[line].split(' =')[0]
    regions[name] = contents[line+1].split('= { ')[1].split(' }')[0].split(' ')

### Load locators
locators = {}
with open('input files/city_locators.txt', 'r') as file:
    contents = file.read().splitlines()
    for line in range(8, len(contents)-4, 6):
        ids = int(contents[line].split("=")[1])
        
        temp = contents[line+1].split(" ")[1:-1]
        locators[ids] = (int(temp[0]), 6144-int(temp[2]))


In [3]:
regionMap = Image.open('input files/regions.png')
display(regionMap)

# K means

In [4]:
def pseudoDistance(pointA, pointB):
    dist, dim = 0, len(pointA)
    for d in range(dim):
        dist += (pointA[d]-pointB[d])**2
    return dist

def KmeansCentering(points: list[tuple], groups: list[int], group: int):
    ind = [i for i, x in enumerate(groups) if x==group]
    n, dim = len(ind), len(points[0])

    return [sum([points[i][d]/n for i in ind]) for d in range(dim)]

def KmeansDistances(point: tuple, centroids: list):
    distances = []
    for center in centroids:
        distances.append(pseudoDistance(point, center))
    nearest = distances.index(min(distances))
    return nearest

def KmeansAssign(points: list[tuple], centroids: list):
    nPoints = len(points)
    groups = [None]*nPoints

    for i, point in enumerate(points):
        groups[i] = KmeansDistances(point, centroids)
        
    return groups

def KmeansCostFunc(points: list[tuple], groups: list[int], centroids: list):
    nPoints = len(points)
    J = 0

    for i, point in enumerate(points):
        index = groups[i]
        J += pseudoDistance(point, centroids[index])

    J = J/nPoints
    return J

def KmeansLloyd(points: list[tuple], k, itera):
    nPoints = len(points)
    selection = np.random.choice(nPoints, k, replace=False)
    centroids = [points[index] for index in selection]

    for i in range(itera):
        groups = KmeansAssign(points, centroids)
        for index in range(k): centroids[index] = KmeansCentering(points, groups, index)

        if i!=0:
            if groups==lastGroups: break
        lastGroups = groups
    
    return centroids, groups

def KmeansHartiganWong(points: list[tuple], k, itera):
    nPoints = len(points)
    centroids = [None]*k

    groups = list(np.random.choice(k, nPoints))
    for index in range(k): centroids[index] = KmeansCentering(points, groups, index)
 
    l=0
    while True:
        for i, point in enumerate(points):
            lastC = groups[i]
            n = groups.count(lastC)
            if n>1: last = [(x*n-point[m])/(n-1) for m, x in enumerate(centroids[lastC])]
            else: last = [0,0]

            costs = []
            for j in range(k):
                newC = j
                if newC==lastC:
                    costs.append(KmeansCostFunc(points, groups, centroids))
                    continue
                p = groups.count(newC)
                next = [(x*p+point[m])/(p+1) for m, x in enumerate(centroids[newC])]

                J = 0
                for m, point2 in enumerate(points):
                    index = groups[m]
                    if m==i: index = newC
                    if index==newC: center = next
                    elif index==lastC: center = last
                    else: center = centroids[index]

                    J += pseudoDistance(point2, center)

                costs.append(J/nPoints)

            newC = costs.index(min(costs))
            if newC==lastC: continue

            n = groups.count(newC)

            groups[i] = newC
            centroids[lastC] = last
            centroids[newC] = [(x*n+point[m])/(n+1) for m, x in enumerate(centroids[newC])]        

        if l!=0:
            if groups==lastGroups: break
        lastGroups = groups
        l+=1
          
    return centroids, groups

def Kmeans(points: list[tuple], k: int, itera: int, method='Hartigan-Wong'):
    
    # 2 methods, naive/Lloyd or Hartigan-Wong
    if method=='Lloyd': method = KmeansLloyd
    elif method=='Hartigan-Wong': method = KmeansHartiganWong
    else: print('Incorrect method')

    for i in range(itera):
        centroids, groups = method(points, k, itera)
        J = KmeansCostFunc(points, groups, centroids)

        if i==0: bestCentroids, bestGroups, bestJ = centroids, groups, J
        elif J < bestJ: bestCentroids, bestGroups, bestJ = centroids, groups, J

    return bestCentroids, bestGroups, bestJ

# COMPUTE

In [5]:
keyRegions = {
    'East_Coast': {'k':5, 'rgb':(180, 115, 110), 'provs':[]},
    'Hudson_Bay': {'k':4, 'rgb':(41, 222, 166), 'provs':[]},
    'Midwest': {'k':8, 'rgb':(251, 236, 133), 'provs':[]},
    'Great_Plains': {'k':9, 'rgb':(187, 22, 146), 'provs':[]},
    'Pacific_Coast': {'k':8, 'rgb':(40, 207, 115), 'provs':[]},
    'Mesoamerica': {'k':8, 'rgb':(196, 96, 33), 'provs':[]},
    'Caribbean': {'k':5, 'rgb':(224, 239, 61), 'provs':[]},
    'Colombia': {'k':5, 'rgb':(164, 178, 107), 'provs':[]},
    'Andes': {'k':10, 'rgb':(180, 155, 55), 'provs':[]},
    'Brazil': {'k':11, 'rgb':(8, 253, 2), 'provs':[]},
    'Guinea': {'k':9, 'rgb':(236, 146, 195), 'provs':[]},
    'Cape': {'k':8, 'rgb':(194, 141, 40), 'provs':[]},
    'The_Horn': {'k':10, 'rgb':(128, 225, 162), 'provs':[]},
    'Tartaria': {'k':9, 'rgb':(123, 136, 222), 'provs':[]},
    'Siberia': {'k':4, 'rgb':(50, 221, 44), 'provs':[]},
    'Terra_Australis': {'k':12, 'rgb':(60, 136, 188), 'provs':[]},
    'Nusantara': {'k':12, 'rgb':(26, 79, 212), 'provs':[]},
    'Champa': {'k':11, 'rgb':(211, 138, 69), 'provs':[]},
    'Cathay': {'k':12, 'rgb':(196, 27, 50), 'provs':[]},
    'Cauli': {'k':2, 'rgb':(214, 214, 107), 'provs':[]},
    'Nippon': {'k':6, 'rgb':(111, 109, 250), 'provs':[]},
    'India': {'k':12, 'rgb':(24, 183, 125), 'provs':[]},
    'Sogdiana': {'k':5, 'rgb':(206, 167, 111), 'provs':[]},
    'Uralia': {'k':5, 'rgb':(167, 222, 60), 'provs':[]},
    'Pontic_Steppe': {'k':7, 'rgb':(138, 251, 149), 'provs':[]},
    'Persia': {'k':8, 'rgb':(91, 163, 196), 'provs':[]},
    'Caucasus': {'k':6, 'rgb':(241, 174, 23), 'provs':[]},
    'Mashriq': {'k':9, 'rgb':(244, 106, 34), 'provs':[]},
    'Arabia': {'k':6, 'rgb':(194, 20, 144), 'provs':[]}
}

# Assign provinces to the desired regions according to the map
for ids in locators:
    color = regionMap.getpixel(locators[ids])
    for reg in keyRegions:
        if keyRegions[reg]['rgb'] == color:
            keyRegions[reg]['provs'].append(ids)
            break

deleteprovs = []
for reg in tqdm(keyRegions):
    provs = keyRegions[reg]['provs']
    deleteprovs.extend(provs)
    points = [locators[ids] for ids in provs]

    k = keyRegions[reg]['k']
    _, area, J = Kmeans(points, k, itera=80)

    keyRegions[reg]['areas'] = area
    

  0%|          | 0/29 [00:00<?, ?it/s]

In [6]:
newareas = {}
deleteareas = []
for area in areas:
    provs = [x for x in areas[area] if x not in deleteprovs]
    if len(provs)==0:
        deleteareas.append(area)
        continue
    newareas[area] = provs

newregions = {}
for reg in regions:
    area = [x for x in regions[reg] if x not in deleteareas]
    if len(area)==0: continue
    newregions[reg] = area

In [7]:
# Add new areas
for reg in keyRegions:
    provs = keyRegions[reg]['provs']
    area = keyRegions[reg]['areas']

    for i in range(max(area)+1):
        newareas[reg+str(i)] = []

    for i in range(len(provs)):
        newareas[reg+str(area[i])].append(provs[i])

    newregions.setdefault(reg, []).extend([reg+str(i) for i in range(max(area)+1)])

In [8]:
descriptions = {}
for i, reg in enumerate(keyRegions):
    if i%2: markers = ['Ultima','Borealis','Superioris','Australis','Inferioris','Occidentalis','Orientalis','Maioris']
    else: markers = ['Ulterior','Septentrionalis','Northern','Meridionalis','Southern','Western','Eastern','Centralis']
    extraMarkers = ['Prima','Secunda','Tertia','Quartia','Quinta','Sexta','Septima','Octavia']

    areaCenters = [list(np.mean([locators[ids] for ids in newareas[area]], axis=0)) for area in newregions[reg]]
    center = list(np.mean(areaCenters, axis=0))
    dists2 = [ np.sqrt(pseudoDistance(point, center)) for point in areaCenters]
    n = len(areaCenters)
    labels = [None]*n

    if n<=4:
        labels[dists2.index(min(dists2))] = 'Maioris'
        labels[dists2.index(max(dists2))] = 'Minoris'
    elif n<8:
        labels[dists2.index(min(dists2))] = markers[7]

        temp = np.argsort([x[1]-center[1] for x in areaCenters])
        if labels[temp[0]]==None: labels[temp[0]] = markers[2]
        if labels[temp[-1]]==None: labels[temp[-1]] = markers[4]

        temp = np.argsort([x[0]-center[0] for x in areaCenters])
        if labels[temp[0]]==None: labels[temp[0]] = markers[5]
        if labels[temp[-1]]==None: labels[temp[-1]] = markers[6]
    else:
        labels[dists2.index(min(dists2))] = markers[7]
        labels[dists2.index(max(dists2))] = markers[0]

        temp = np.argsort([x[1]-center[1] for x in areaCenters])
        if labels[temp[0]]==None: labels[temp[0]] = markers[1]
        if labels[temp[-1]]==None: labels[temp[-1]] = markers[3]

        temp = np.argsort([x[0]-center[0] for x in areaCenters])
        if labels[temp[0]]==None: labels[temp[0]] = markers[5]
        if labels[temp[-1]]==None: labels[temp[-1]] = markers[6]

        temp = np.argsort([x[1]-center[1] for x in areaCenters])
        if labels[temp[1]]==None: labels[temp[1]] = markers[2]
        if labels[temp[-2]]==None: labels[temp[-2]] = markers[4]

    m = 0
    for j in range(n):
        if labels[j]==None:
            labels[j] = extraMarkers[m]
            m+=1

    for j, area in enumerate(newregions[reg]):
        descriptions[area] = labels[j]

# SAVING

In [9]:
shuffled_regions = list(newregions.keys())
np.random.shuffle(shuffled_regions)
with open('output files/regions.txt', 'w') as file:
    for reg in shuffled_regions:
        file.write(reg+'_region = { #'+str(len(newregions[reg]))+'\n\tareas = { ')
        for area in newregions[reg]: file.write(area+'_area ')
        file.write('}\n}\n\n')

with open('output files/areas.txt', 'w') as file:
    for area in newareas:
        file.write(area+'_area = { #'+str(len(newareas[area]))+'\n\tprovinces = { ')
        for ids in newareas[area]: file.write(str(ids)+' ')
        file.write('}\n}\n\n')

In [10]:
### Write localization
with open('output files/regionnames_l_english.yml', 'w') as file:
    file.write('l_english:\n')
    for reg in newregions:
        name = reg.replace('_', ' ')
        file.write(f' {reg}_region:0 "{name}"\n')
    for area in newareas:
        if area in descriptions:
            label = descriptions[area]
            if label=='Northern' or label=='Southern' or label=='Western' or label=='Eastern':
                name = label+' '+area.replace('_', ' ')
            else:
                name = area.replace('_', ' ')+' '+label
        else:
            name = area.replace('_', ' ')
        for character in name:
            if character.isdigit(): name = name.replace(character, '')
        file.write(f' {area}_area:0 "{name}"\n')